https://github.com/MichaelAllen1966/learninghospital/blob/master/simpy_envs/env_simple_hospital_bed_1.py

I recently came across this simulation implementation of this study where they used SimPy and were able to work it within a `step` framework. 

I read through the study and I found that the key idea that enabled it was that the `env.run()` was inside the `step()` function. And the key idea is *drumrolls* that the environment is run only for one time step at a time (or a constant number of time steps) 

I'm going to try and implement this using the environment that I have on SimPy already. 

# Notes

Current problems/questions
- When an action is rejected, we have to pause the production. Currently it is not pausing. It is going ahead with the next first product in the queue. [More info](https://simpy.readthedocs.io/en/latest/topical_guides/process_interaction.html#sleep-until-woken-up)
    

-----

Solved problems
- `prod_and_requests` is empty when checking for check_env function. Look into it
    - This is because i'm appending to prod_and_requests inside the envGym but while checking the env, envGym is not defined. This is the problem. Why do I have envGym inside the class?
- What is the flow of the current customEnv?
- How to ensure that the action suggested by DQN is taken by the algorithm?
    - Print action taken (Step function)
    - Print action chosen by the RL agent
    - SOLVED: Now I use the same variable `self.current_action` to record the input action and then execute it when necessary. 

# OpenAI Gym environment 

Gym format 

## Choosing a product environment 

In [ ]:
import gym
from gym import spaces
import numpy as np 
import simpy 
import random



In [ ]:
import gym
from gym import spaces
import numpy as np 
import simpy 
import random

 
        
class CustomEnv(gym.Env):
    metadata = {'render.modes': ['human']}
    def __init__(self):
        super(CustomEnv, self).__init__()
        #random.seed(42)
        # Define action and observation space
        # They must be gym.spaces objects
        # Example when using discrete actions:

        # initially the observation space is zero. I will append as the products are initialized.
        #print("Observation space sample ",self.observation_space.sample())
        #self.observation_space = spaces.Box(low=0, high=255,shape=(2, 2), dtype=np.uint8)
##------------------------------------------------------------------------------------------------
##----------------------------------------SIMPY STUFF---------------------------------------------
##------------------------------------------------------------------------------------------------

        
#        self.action = env.process(self.production())
        self.NUM_PRODUCTS = 20
        self.next_time_stop = 0
        self.prod_and_requests = []
        # Defining the observation and action spaces 
        # action space for choosing product 
         self.action_space = spaces.Discrete(self.NUM_PRODUCTS)
        # action space for Yes/No action space 
        # self.action_space = spaces.Discrete(2)
        self.observation_space = spaces.Box(0,1,shape = (self.NUM_PRODUCTS,1),
                                            dtype = np.float32)
    
    def getObservation(self):
        # Calculate the states 
        states = []
        if self.machine.queue != None:
            for i in (self.machine.queue):
                states.append((self.relater(i)).number)
        #Checking the length of the states and filling the rest with zeros
        if len(states) < self.NUM_PRODUCTS:
            for i in range(self.NUM_PRODUCTS - len(states)):
                states.append(0)
        states = np.array(states).reshape(self.NUM_PRODUCTS,1)
        return states
    
    def doneFn(self):
        # So the condition is, 
        #(no items in queue1 + queue2 + ...) AND 
        #(no machine is running)
        if self.machine.queue != None:
            lenQueue = len(self.machine.queue )
        else:
            lenQueue = 0 
        lenMachinesUsed = self.machine.count
        if lenQueue == 0 and lenMachinesUsed == 0:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return True
        else:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return False
    
    def step(self):
        self.action_taken = False 
        self.info = {}
        self.next_time_stop += self.time_step
        self.envSimpy.run(until =self.next_time_stop)

        # Calculate states
        observation = self.getObservation()
        reward = 1 
        done = self.doneFn()
        info = self.info
        if self.action_taken == True:
            #print("Taking this action ", self.action)
            pass
        else:
            pass
            #print('No action was taken')
        return observation, reward, done, info
    # ----------------------------------------------------------------
    def reset(self):
        self.envSimpy = simpy.Environment()
        self.machine = simpy.Resource(self.envSimpy,capacity = 1)
        self.time_start = self.envSimpy.now
        print("This is the time ",self.time_start)
        self.next_time_stop = self.time_start + 2
        self.time_step = 1 
        self.time_step_terminal = self.time_start + 100
        self.current_action = 0
        print('the time now is ', self.time_start)
        
        self.instances = []
        for i in range(self.NUM_PRODUCTS):
            self.instances.append(self.product(self,self.envSimpy,'Product_%d' % i,i/100, self.machine))
        # i is divided by hundred because the number has to obey the observation_space criteria which is 1 to 1. 
        self.observation = self.getObservation()
        
        return np.array(self.observation)  # reward, done, info can't be included

    
    def render(self, mode='human'):
        myFrame = ""
        #myFrame = "_:_:_:_:_:_:_:_:01:19:18:_:01:02:03::|02|"
        
        for item in enumerate(self.machine.queue):
            product = self.relater(item[1])
            myFrame = myFrame + str(int((product.number)*100)) +':'
        for i in range(self.NUM_PRODUCTS-len(self.machine.queue)):
            myFrame = myFrame + 'x' +':'
        if self.relater(self.machine.users[0]) == None:
            prod_in_machine = 0
            machine_text = prod_in_machine 
        else:
            prod_in_machine = self.relater(self.machine.users[0])
            machine_text = int(prod_in_machine.number*100)
        myFrame = myFrame + ":|" + str(machine_text) + "|"
        return myFrame
    
    def close (self):
        return True
    
    # write the following functions
    
    
    def isLegal(self,action):
        return
    def isExecutable(self, action):
        return True 
    def interpretQueue(self):
        return True 
    def choose_action(self):
            # sampling until we get a legal action
        while True:
            self.action = envGym.action_space.sample()
            if (envGym.machine.queue != None):
                if len(envGym.machine.queue) != 0:
                    if len(envGym.machine.queue)-1 < self.action:
                        # the action is illegal -> sample again
                        #print("machine queue is ", envGym.machine.queue)
                        #print("length of machine queue ",len(envGym.machine.queue)-1,"action " , self.action )
                        pass
                    else:
                        break
                else:
                    self.action = None
                    break
        return self.action
    
    def take_action(self):
        # arrange the self.machine.queue based on the self.current_action
        # to do 
        # Do something about illegal action
        if self.current_action != None:
            if self.machine.queue != None:
                # rearrange queue
                #print("Initial queue with length  ", len(self.machine.queue))
                #print("test4 queue ", len(self.machine.queue), "action " , self.current_action)
                product_high_priority = (self.machine.queue)[(self.current_action)]
                #print("high priority product ", product_high_priority, "Position was ", self.current_action)
                (self.machine.queue).pop(self.current_action)
                self.machine.queue.insert(0,product_high_priority)
                #print("Edited queue ")

                # change the action_taken bit 
                #print('Does the queue length remain the same ?', len(self.machine.queue))
                envGym.action_taken = True
                return self.machine.queue
            else: 
                self.info = {"Queue is empty, no action taken"}
                #print("Queue is empty, no action taken")
                return self.machine.queue
        else:
            return self.machine.queue
       

    # A function to relate products and requests
    def relater(self,item):
        output_item = None

        if type(item) == simpy.resources.resource.Request:
            for i, j in enumerate(self.prod_and_requests):
                if j[1] == item:
                    output_item = j[0]
                    return output_item
        else:
            #print('Input Process object is ')
            for i, j in enumerate(self.prod_and_requests):
                if j[0] == item:
                    output_item = j[1]
                    return output_item

    class product(object):
        def __init__(self, envGym, envSimpy, name, number, machine):
            # Creating the required resources and environment
            self.envSimpy = envSimpy
            self.prod_type = random.randint(1,3) # the product type of the product.
            self.prod_state = 1 # the state of production. 1 implies raw material. 2 implies first operation done and so on. 
            self.production_time = random.randint(1,8)  
            self.name = name
            self.number = number
            self.machine = machine 
            self.production_end = random.randint(1,90)
            self.action = self.envSimpy.process(self.production())

            # move this into the main class
        def production(self):
            # the first step in production is requesting for a machine
            #print('entered production ' + self.name)
            with self.machine.request() as req:
                envGym.prod_and_requests.append([self,req])
                #print('waiting for the request to succeed ' + str(self.name))
                yield req
                print('Start production of ' + str(self.name) + ' at '+ str(self.envSimpy.now)  )
                print('Production time is ' + str(self.production_time))
                yield self.envSimpy.timeout(self.production_time)
                self.tardiness = self.production_end - self.envSimpy.now
                # End of production
                print('End production of ' + str(self.name) + ' at ' + str(self.envSimpy.now))
                print('\n')
                # Taking the chosen action
                envGym.current_action = envGym.choose_action()
                envGym.machine.queue = envGym.take_action()
            #print('Remaining products to produce ')
            #print((self.machine.queue)) 



## Yes/No Environment

In [63]:
import gym
from gym import spaces
import numpy as np 
import simpy 
import random

In [64]:
observation_space = spaces.Box(0,1,shape = (20,),
                                            dtype = np.float32)

In [65]:
print(observation_space.low)

[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]


In [1]:
class CustomEnv(gym.Env):
    metadata = {'render.modes': ['human']}
    def __init__(self):
        super(CustomEnv, self).__init__()
        #random.seed(42)
        # Define action and observation space
        # They must be gym.spaces objects
        # Example when using discrete actions:

        # initially the observation space is zero. I will append as the products are initialized.
        #print("Observation space sample ",self.observation_space.sample())
        #self.observation_space = spaces.Box(low=0, high=255,shape=(2, 2), dtype=np.uint8)
##------------------------------------------------------------------------------------------------
##----------------------------------------SIMPY STUFF---------------------------------------------
##------------------------------------------------------------------------------------------------

        
#        self.action = env.process(self.production())
        self.NUM_PRODUCTS = 20
        self.next_time_stop = 0
        self.prod_and_requests = []
        self.reward = 0
        self.cumulative_reward = 0
        # Defining the observation and action spaces 
        # action space for choosing product 
        # self.action_space = spaces.Discrete(self.NUM_PRODUCTS)
        # action space for Yes/No action space 
        self.action_space = spaces.Discrete(2)
        self.observation_space = spaces.Discrete(20)
        #self.observation_space = spaces.Box(0,1,shape = (self.NUM_PRODUCTS,),
        #                                    dtype = np.float32)
    
    
    
    
    def getObservation(self):
        # Calculate the states 
        states = []
        if self.machine.queue:
            for i in (self.machine.queue):
                states.append(((self.relater(i)).number)*100)
        
        #Checking the length of the states and filling the rest with zeros
        if len(states) < self.NUM_PRODUCTS:
            for i in range(self.NUM_PRODUCTS - len(states)):
                states.append(0)
        states = np.array(states).reshape(self.NUM_PRODUCTS,1)
        
        states = states.flatten()
        return states
    

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------OpenAI Gym functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    
    def step(self, action):
        print("Agent is suggesting an action")
        #print("-------------------------------------------------------------------------------")
        #print("Action chosen by the RL agent ", action)
        
        # Define params
        self.current_action = action
        self.action_taken = False 
        self.info = {}
        #print("Current user of the machine ", envGym.machine.users)
        #print(envGym.machine.queue)
        print('action is ', self.current_action)
        print('#observation_before')
        print(envGym.getObservation())
        
        
        if self.current_action == 1:
            # rearrange the machine queue to reflect the rejection
            self.machine.queue.insert(len(self.machine.queue), self.machine.queue.pop(0))
        else:
            pass
        
        # print the rearranged machine queue
        print('#observation_after')
        print(envGym.getObservation())
        
        self.next_time_stop += self.time_step
        self.envSimpy.run(until = self.next_time_stop)
        #print("#comparing machine queues")
        #print('machine queue outside', self.getObservation()) 
        
        #if self.action_taken == False:
            #print("Machine is running so no action taken")
        # Get the observation states
        observation = self.getObservation()
        done = self.doneFn()
        info = self.info
        self.cumulative_reward += self.reward
        
        return observation, self.reward, done, info
    
    # ----------------------------------------------------------------
    def reset(self):
        self.envSimpy = simpy.Environment()
        self.machine = simpy.Resource(self.envSimpy,capacity = 1)
        self.time_start = self.envSimpy.now
        self.next_time_stop = self.time_start + 1
        self.time_step = 1 
        self.time_step_terminal = self.time_start + 100
        self.current_action = 0
        self.instances = []
        
        for i in range(self.NUM_PRODUCTS):
            self.instances.append(self.product(self,self.envSimpy,'Product_%d' % i,i/100, self.machine))
        
        # i is divided by hundred because the number has to obey the observation_space criteria which is 1 to 1. 
        self.observation = self.getObservation()
        
        return np.array(self.observation)  # reward, done, info can't be included

    
    def render(self, mode='human'):
        myFrame = ""
        #myFrame = "_:_:_:_:_:_:_:_:01:19:18:_:01:02:03::|02|"
        
        for item in enumerate(self.machine.queue):
            product = self.relater(item[1])
            myFrame = str(int((product.number)*100)) +':'+ myFrame
        for i in range(self.NUM_PRODUCTS-len(self.machine.queue)):
            myFrame =  'x' +':' + myFrame
        if self.relater(self.machine.users[0]) == None:
            prod_in_machine = 0
            machine_text = prod_in_machine 
        else:
            prod_in_machine = self.relater(self.machine.users[0])
            machine_text = int(prod_in_machine.number*100)
        myFrame = myFrame +  "  |" + str(machine_text) + "|"
        return myFrame

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Miscellaneous functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    def doneFn(self):
        # So the condition is, 
        #(no items in queue1 + queue2 + ...) AND 
        #(no machine is running)
        
        if self.machine.queue != None:
            lenQueue = len(self.machine.queue)
        else:
            lenQueue = 0 
        lenMachinesUsed = self.machine.count
        if lenQueue == 0 and lenMachinesUsed == 0:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return True
        else:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return False
        
    # A function to relate products and requests
    def relater(self,item):
        output_item = None
        # If the input is a request
        if type(item) == simpy.resources.resource.Request:
            for i, j in enumerate(self.prod_and_requests):
                if j[1] == item:
                    output_item = j[0]
                    return output_item
        else: #if the input is a product 
            for i, j in enumerate(self.prod_and_requests):
                if j[0] == item:
                    output_item = j[1]
                    return output_item    

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Action related functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    def choose_action(self):
        # sampling until we get a legal action
        self.action = envGym.action_space.sample()
        return self.action
    
    def take_action(self):
        # arrange the self.machine.queue based on the self.current_action
        self.action_taken = True 
        if self.machine.queue: # if the machine queue is not empty
            if self.current_action == 0: # if the answer is accepted
                # Output the same machine.queue
                return self.machine.queue # return the machine queue as is
            elif self.current_action == 1: # if the answer is rejected
                # rearrange the machine queue 
                
                # Take the first element in the machine queue and put it in the last pos. 
                self.machine.queue.insert(len(self.machine.queue), self.machine.queue.pop(0))
                
                return self.machine.queue
        else:
            return self.machine.queue

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Product class definition--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------

    class product(object):
        def __init__(self, envGym, envSimpy, name, number, machine):
            
            # Creating the required resources and environment
            self.envSimpy = envSimpy
            self.prod_type = random.randint(1,3) # the product type of the product.
            self.prod_state = 1 # the state of production. 1 implies raw material. 2 implies first operation done and so on. 
            self.production_time = random.randint(1,8)  
            self.name = name
            self.number = number
            self.machine = machine 
            self.production_end = random.randint(1,90)
            self.action = self.envSimpy.process(self.production())
            
            #self.action_taken_event = envSimpy.event
            # Defining Events        
            #self.action_accepted_event = envSimpy.event()            
            # Defining processes
            #self.check_accepted_proc = envSimpy.process(self.check_accepted(envSimpy))


            
        def production(self):
            # the first step in production is requesting for a machine
            #print('entered production ' + self.name)
            with self.machine.request() as req:
                envGym.prod_and_requests.append([self,req])
                #print('waiting for the request to succeed ' + str(self.name))
                yield req
                print('Start production of ' + str(self.name) + ' at '+ str(self.envSimpy.now)  )
                #print("Request of the product ", envGym.relater(self))
                print('Production time is ' + str(self.production_time))
                yield self.envSimpy.timeout(self.production_time)
                self.tardiness = self.envSimpy.now - self.production_end   # -ve is good; +ve is bad 
                
                # End of production 
                print('End production of ' + str(self.name) + ' at ' + str(self.envSimpy.now))
                
                # Pass time when the action chosen by the agent is rejection
                i = 0
                while True:
                    i += 1
                    print("envGym.current_action",envGym.current_action)
                    if envGym.current_action == 1: #rejected
                        yield self.envSimpy.timeout(1)
                        
                        #print('#observation_before')
                        print(envGym.getObservation())
                        
                        
                        # rearrange the machine queue to reflect the rejection
                        self.machine.queue.insert(len(self.machine.queue), self.machine.queue.pop(0))
                        
                        
                        # print the rearranged machine queue
                        #print('#observation_after')
                        #print(envGym.getObservation())
                        
                        print("Action rejected; Passing time by 1 ", i)
                        
                    else: #if action accepted
                        print("Action accepted")
                        break
                
                # Decide the reward 
                if self.tardiness > 0:
                    envGym.reward = 10 
                else: 
                    envGym.reward = 0
                # Production has ended now I have to take the next action using take_action()
                # envGym.machine.queue = envGym.take_action()
                #envGym.machine.queue = []
                
        def check_accepted(self, envSimpy): # sleep and production
            while True: # check in a continuous loop 
                if envGym.current_action == 0: # Is action accepted?
                    print("Action is accepted")
                    # Unsleeping the process 
                    self.action_accepted_event.succeed()
                    self.action_accepted_event = envSimpy.event()            
                else:
                    print("Action is rejected")
                    pass
        
        def passivate_production(self):
            while True:
                print("Passivating production at ", self.envSimpy.now)
                yield self.reactivate_production
                print("Production reactivate at ", self.envSimpy.now)
            #print('Remaining products to produce ')
            #print((self.machine.queue)) 

NameError: name 'gym' is not defined

## Testing the environment 

In [ ]:
import gym
from gym import error, spaces, utils
from gym.utils import seeding
#random.seed(42)
envGym = CustomEnv()
obs = envGym.reset()
frames = [] # for animation

# Add another while loop above the current one for EPOCHS
while True: # This while is for one full cycle of products (20 nos, currently)

    # Choosing the action
    action = envGym.action_space.sample() # Random agent
    #action = 0 #FIFO
    # Taking a step

    obs, reward, done, info = envGym.step(action) # the env here is gym
    # Note that in the above step function, i'm passing 1. 
    # It has no relevance to the action that will be taken. It is just to satisfy the OpenAI Gym requirements
    #print("Action chosen by the agent ", action)
    #print("Action taken by the environment ", )
    if done:
        print("Goal reached! ", "reward= ", reward)
        print("The env time is ", envGym.envSimpy.now)
        sum_Tardiness = 0 
        for i in range(20):
            #print(envGym.instances[i].tardiness)
            sum_Tardiness = sum_Tardiness + envGym.instances[i].tardiness
            print('Tardiness value of ', i, 'is ',envGym.instances[i].tardiness )
            
        print('Mean tardiness for this episode is ', sum_Tardiness)
        print('Total reward for this episode is ', envGym.cumulative_reward)
        break
    else:
        print('render append',obs)
        frames.append({
            'frame': envGym.render(mode='ansi'),
            'state': obs,
            'action': envGym.current_action,
            'reward': reward
            }
        )        

### Rendering

In [ ]:
from IPython.display import clear_output
from time import sleep

def print_frames(frames):
    for i, frame in enumerate(frames):
        clear_output(wait=True)
        print(frame['frame'], frame['action'], i)
        #print(f"Timestep: {i + 1}")
        #print(f"State: {frame['state']}")
        #print(f"Action: {frame['action']}")
        #print(f"Reward: {frame['reward']}")
        sleep(0.7)
        
print_frames(frames)

Calculating the tardiness

The following is the code to test if the environment conforms to the OpenAI format. 

In [68]:
from stable_baselines.common.env_checker import check_env
random.seed(42)
envGym = CustomEnv()
# It will check your custom environment and output additional warnings if needed
check_env(envGym, warn= True)

/Users/suguthansekar/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:523: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/Users/suguthansekar/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:524: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/Users/suguthansekar/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:525: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/Users/suguthansekar/.local/lib/python3.6/site-packages/tensorflow/

AssertionError: The observation returned by `reset()` method must be an int

# RL Algorithms

## Q Learning

In [48]:
random.seed(42)
env = CustomEnv()
#Setting the hyperparameters
              
alpha = 0.7 #learning rate                 
discount_factor = 0.618               
epsilon = 1                  
max_epsilon = 1
min_epsilon = 0.01         
decay = 0.01

train_episodes = 2000    
test_episodes = 100          
max_steps = 100

In [49]:
#Initializing the Q-table

Q = np.zeros((env.observation_space.n, env.action_space.n))

In [50]:
#Creating lists to keep track of reward and epsilon values

training_rewards = []  
epsilons = []

for episode in range(train_episodes):
    #Reseting the environment each time as per requirement
    state = env.reset()    
    #Starting the tracker for the rewards
    total_training_rewards = 0
    for step in range(100):
        #Choosing an action given the states based on a random number
        exp_exp_tradeoff = random.uniform(0, 1) 
        
### STEP 2: SECOND option for choosing the initial action - exploit     
        #If the random number is larger than epsilon: employing exploitation 
        #and selecting best action 
        if exp_exp_tradeoff > epsilon:
            action = np.argmax(Q[state,:]) 
            
### STEP 2: FIRST option for choosing the initial action - explore       
        #Otherwise, employing exploration: choosing a random action 
        else:
            action = env.action_space.sample()
        ### STEPs 3 & 4: performing the action and getting the reward     

        #Taking the action and getting the reward and outcome state
        new_state, reward, done, info = env.step(action)
        
        
        
        ### STEP 5: update the Q-table

#Updating the Q-table using the Bellman equation
        Q[state, action] = Q[state, action]+alpha*(reward+discount_factor*
        np.max(Q[new_state, :])-Q[state, action]) 
        #Increasing our total reward and updating the state
        total_training_rewards += reward      
        state = new_state         
        
        #Ending the episode
        if done == True:
            #print ("Total reward for episode {}: {}".format(episode, 
            #total_training_rewards))
            break
    
    #Cutting down on exploration by reducing the epsilon 
    epsilon = min_epsilon+(max_epsilon-min_epsilon)*np.exp(-decay*episode)
    
    #Adding the total reward and reduced epsilon values
    training_rewards.append(total_training_rewards)
    epsilons.append(epsilon)
print ("Training score over time: " + str(sum(training_rewards)/train_episodes))

asdf  []
Agent is suggesting an action
Start production of Product_0 at 0
Production time is 2
Machine is running so no action taken
asdf  [<Request() object at 0x1323e0978>, <Request() object at 0x132308860>, <Request() object at 0x1323084a8>, <Request() object at 0x132308a58>, <Request() object at 0x132308240>, <Request() object at 0x132308668>, <Request() object at 0x1323081d0>, <Request() object at 0x1323082b0>, <Request() object at 0x132308160>, <Request() object at 0x132308908>, <Request() object at 0x132308048>, <Request() object at 0x1323089b0>, <Request() object at 0x13233e160>, <Request() object at 0x1322e4c88>, <Request() object at 0x1322e4710>, <Request() object at 0x1322e4908>, <Request() object at 0x1322e4390>, <Request() object at 0x1322e4128>, <Request() object at 0x1322e4940>]


AttributeError: 'NoneType' object has no attribute 'number'

In [ ]:
  #Cutting down on exploration by reducing the epsilon 
 
    epsilon = min_epsilon+(max_epsilon-min_epsilon)*np.exp(-decay*episode)
    
    #Adding the total reward and reduced epsilon values
    training_rewards.append(total_training_rewards)
    epsilons.append(epsilon)
    
print ("Training score over time: " + str(sum(training_rewards)/train_episodes))

## DQN

In [4]:
envGym.reset()

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0])

In [5]:
import gym
from stable_baselines import DQN
from stable_baselines.common.evaluation import evaluate_policy



/Users/suguthansekar/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:523: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/Users/suguthansekar/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:524: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/Users/suguthansekar/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:525: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/Users/suguthansekar/.local/lib/python3.6/site-packages/tensorflow/

### Training the RL model

In [6]:
%%time
# Instantiate the agent
model = DQN('MlpPolicy', envGym, learning_rate=1e-3, prioritized_replay=True, verbose=1)
# Train the agent
model.learn(total_timesteps= 10000) #int(2e5))
# Save the agent
model.save("dqn_jobshop")
del model  # delete trained model to demonstrate loading

New action from the agent
Start production of Product_0 at 0
Production time is 2
New action from the agent
End production of Product_0 at 2
Action accepted
Start production of Product_1 at 2
Production time is 4
New action from the agent
New action from the agent
New action from the agent
New action from the agent
End production of Product_1 at 6
New action from the agent
Action rejected; Passing time by 0.1  1
Action accepted
Start production of Product_2 at 7
Production time is 8
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
End production of Product_2 at 15
Action accepted
Start production of Product_3 at 15
Production time is 7
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
End production 

New action from the agent
End production of Product_13 at 69
New action from the agent
Action rejected; Passing time by 0.1  1
Action accepted
Start production of Product_14 at 70
Production time is 8
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
End production of Product_14 at 78
Action accepted
Start production of Product_15 at 78
Production time is 2
New action from the agent
New action from the agent
End production of Product_15 at 80
Action accepted
Start production of Product_16 at 80
Production time is 5
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
End production of Product_16 at 85
Action accepted
Start production of Product_17 at 85
Production time is 3
New action from the agent
New action from the agent
New action from the agent
End 

New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
End production of Product_4 at 33
Action accepted
Start production of Product_5 at 33
Production time is 2
New action from the agent
New action from the agent
End production of Product_5 at 35
New action from the agent
Action rejected; Passing time by 0.1  1
Action accepted
Start production of Product_6 at 36
Production time is 8
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
End production of Product_6 at 44
New action from the agent
Action rejected; Passing time by 0.1  1
Action accepted
Start production of Product_7 at 45
Production time is 7
New action from the agent
New action from the agent
New action from the agent
N

New action from the agent
Action rejected; Passing time by 0.1  1
New action from the agent
Action rejected; Passing time by 0.1  2
New action from the agent
Action rejected; Passing time by 0.1  3
Action accepted
Start production of Product_3 at 18
Production time is 5
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
End production of Product_3 at 23
New action from the agent
Action rejected; Passing time by 0.1  1
Action accepted
Start production of Product_4 at 24
Production time is 8
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
End production of Product_4 at 32
New action from the agent
Action rejected; Passing time by 0.1  1
New action from the agent
Action rejected; Passing time by 0.1  2
New action from the agent
Action rejected; Passing t

New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
End production of Product_16 at 94
Action accepted
Start production of Product_17 at 94
Production time is 5
New action from the agent
New action from the agent
New action from the agent
New action from the agent
New action from the agent
End production of Product_17 at 99
New action from the agent
Action rejected; Passing time by 0.1  1
New action from the agent
Action rejected; Passing time by 0.1  2
New action from the agent
Action rejected; Passing time by 0.1  3
New action from the agent
Action rejected; Passing time by 0.1  4
New action from the agent
Action rejected; Passing time by 0.1  5
New action from the agent
Action rejected; Passing time by 0.1  6
New action from the agent
Action rejected; Passing time by 0.1  7
New action from the agent
Action rejected; Passing time by 0.1  8
New action from 

...

New action from the agent
Action rejected; Passing time by 0.1  91
New action from the agent
Action rejected; Passing time by 0.1  92
New action from the agent
Action rejected; Passing time by 0.1  93
New action from the agent
Action rejected; Passing time by 0.1  94
New action from the agent
Action rejected; Passing time by 0.1  95
New action from the agent
Action rejected; Passing time by 0.1  96
New action from the agent
Action rejected; Passing time by 0.1  97
New action from the agent
Action rejected; Passing time by 0.1  98
New action from the agent
Action rejected; Passing time by 0.1  99
New action from the agent
Action rejected; Passing time by 0.1  100
New action from the agent
Action rejected; Passing time by 0.1  101
New action from the agent
Action rejected; Passing time by 0.1  102
New action from the agent
Action rejected; Passing time by 0.1  103
New action from the agent
Action rejected; Passing time by 0.1  104
New action from the agent
Action rejected; Passing time b

New action from the agent
Action rejected; Passing time by 0.1  225
New action from the agent
Action rejected; Passing time by 0.1  226
New action from the agent
Action rejected; Passing time by 0.1  227
New action from the agent
Action rejected; Passing time by 0.1  228
New action from the agent
Action rejected; Passing time by 0.1  229
New action from the agent
Action rejected; Passing time by 0.1  230
New action from the agent
Action rejected; Passing time by 0.1  231
New action from the agent
Action rejected; Passing time by 0.1  232
New action from the agent
Action rejected; Passing time by 0.1  233
New action from the agent
Action rejected; Passing time by 0.1  234
New action from the agent
Action rejected; Passing time by 0.1  235
New action from the agent
Action rejected; Passing time by 0.1  236
New action from the agent
Action rejected; Passing time by 0.1  237
New action from the agent
Action rejected; Passing time by 0.1  238
New action from the agent
Action rejected; Passi

New action from the agent
Action rejected; Passing time by 0.1  76
New action from the agent
Action rejected; Passing time by 0.1  77
New action from the agent
Action rejected; Passing time by 0.1  78
New action from the agent
Action rejected; Passing time by 0.1  79
New action from the agent
Action rejected; Passing time by 0.1  80
New action from the agent
Action rejected; Passing time by 0.1  81
New action from the agent
Action rejected; Passing time by 0.1  82
New action from the agent
Action rejected; Passing time by 0.1  83
New action from the agent
Action rejected; Passing time by 0.1  84
New action from the agent
Action rejected; Passing time by 0.1  85
New action from the agent
Action rejected; Passing time by 0.1  86
New action from the agent
Action rejected; Passing time by 0.1  87
New action from the agent
Action rejected; Passing time by 0.1  88
New action from the agent
Action rejected; Passing time by 0.1  89
New action from the agent
Action rejected; Passing time by 0.1

New action from the agent
Action rejected; Passing time by 0.1  46
New action from the agent
Action rejected; Passing time by 0.1  47
New action from the agent
Action rejected; Passing time by 0.1  48
New action from the agent
Action rejected; Passing time by 0.1  49
New action from the agent
Action rejected; Passing time by 0.1  50
New action from the agent
Action rejected; Passing time by 0.1  51
New action from the agent
Action rejected; Passing time by 0.1  52
New action from the agent
Action rejected; Passing time by 0.1  53
New action from the agent
Action rejected; Passing time by 0.1  54
New action from the agent
Action rejected; Passing time by 0.1  55
New action from the agent
Action rejected; Passing time by 0.1  56
New action from the agent
Action rejected; Passing time by 0.1  57
New action from the agent
Action rejected; Passing time by 0.1  58
New action from the agent
Action rejected; Passing time by 0.1  59
New action from the agent
Action rejected; Passing time by 0.1

New action from the agent
Action rejected; Passing time by 0.1  22
New action from the agent
Action rejected; Passing time by 0.1  23
New action from the agent
Action rejected; Passing time by 0.1  24
New action from the agent
Action rejected; Passing time by 0.1  25
New action from the agent
Action rejected; Passing time by 0.1  26
New action from the agent
Action rejected; Passing time by 0.1  27
New action from the agent
Action rejected; Passing time by 0.1  28
New action from the agent
Action rejected; Passing time by 0.1  29
New action from the agent
Action rejected; Passing time by 0.1  30
New action from the agent
Action rejected; Passing time by 0.1  31
New action from the agent
Action rejected; Passing time by 0.1  32
New action from the agent
Action rejected; Passing time by 0.1  33
New action from the agent
Action rejected; Passing time by 0.1  34
New action from the agent
Action rejected; Passing time by 0.1  35
New action from the agent
Action rejected; Passing time by 0.1

### Loading the training RL model

In [11]:
# Load the trained agent
model = DQN.load("dqn_jobshop")

# Evaluate the agent
#mean_reward, std_reward = evaluate_policy(model, envGym, n_eval_episodes=10)
#print(mean_reward, std_reward)
# Enjoy trained agent
obs = envGym.reset()
while dones==False:
    action, _states = model.predict(obs)
    obs, rewards, dones, info = envGym.step(action)
    print(dones)
#envGym.render()

Loading a model without an environment, this model cannot be trained until it has a valid environment.
New action from the agent
Start production of Product_0 at 0
Production time is 1
End production of Product_0 at 1
False
New action from the agent
Action rejected; Passing time by 0.1  1
Action accepted
Start production of Product_1 at 2
Production time is 1
False
New action from the agent
End production of Product_1 at 3
Action accepted
Start production of Product_2 at 3
Production time is 5
False
New action from the agent
False
New action from the agent
False
New action from the agent
False
New action from the agent
False
New action from the agent
End production of Product_2 at 8
Action accepted
Start production of Product_3 at 8
Production time is 6
False
New action from the agent
False
New action from the agent
False
New action from the agent
False
New action from the agent
False
New action from the agent
False
New action from the agent
End production of Product_3 at 14
Action acc

False
New action from the agent
Action rejected; Passing time by 0.1  96
False
New action from the agent
Action rejected; Passing time by 0.1  97
False
New action from the agent
Action rejected; Passing time by 0.1  98
False
New action from the agent
Action rejected; Passing time by 0.1  99
False
New action from the agent
Action rejected; Passing time by 0.1  100
False
New action from the agent
Action rejected; Passing time by 0.1  101
False
New action from the agent
Action rejected; Passing time by 0.1  102
False
New action from the agent
Action rejected; Passing time by 0.1  103
False
New action from the agent
Action rejected; Passing time by 0.1  104
False
New action from the agent
Action rejected; Passing time by 0.1  105
False
New action from the agent
Action rejected; Passing time by 0.1  106
False
New action from the agent
Action rejected; Passing time by 0.1  107
False
New action from the agent
Action rejected; Passing time by 0.1  108
False
New action from the agent
Action rej

New action from the agent
Action rejected; Passing time by 0.1  214
False
New action from the agent
Action rejected; Passing time by 0.1  215
False
New action from the agent
Action rejected; Passing time by 0.1  216
False
New action from the agent
Action rejected; Passing time by 0.1  217
False
New action from the agent
Action rejected; Passing time by 0.1  218
False
New action from the agent
Action rejected; Passing time by 0.1  219
False
New action from the agent
Action rejected; Passing time by 0.1  220
False
New action from the agent
Action rejected; Passing time by 0.1  221
False
New action from the agent
Action rejected; Passing time by 0.1  222
False
New action from the agent
Action rejected; Passing time by 0.1  223
False
New action from the agent
Action rejected; Passing time by 0.1  224
False
New action from the agent
Action rejected; Passing time by 0.1  225
False
New action from the agent
Action rejected; Passing time by 0.1  226
False
New action from the agent
Action rejec

False
New action from the agent
Action rejected; Passing time by 0.1  334
False
New action from the agent
Action rejected; Passing time by 0.1  335
False
New action from the agent
Action rejected; Passing time by 0.1  336
False
New action from the agent
Action rejected; Passing time by 0.1  337
False
New action from the agent
Action rejected; Passing time by 0.1  338
False
New action from the agent
Action rejected; Passing time by 0.1  339
False
New action from the agent
Action rejected; Passing time by 0.1  340
False
New action from the agent
Action rejected; Passing time by 0.1  341
False
New action from the agent
Action rejected; Passing time by 0.1  342
False
New action from the agent
Action rejected; Passing time by 0.1  343
False
New action from the agent
Action rejected; Passing time by 0.1  344
False
New action from the agent
Action rejected; Passing time by 0.1  345
False
New action from the agent
Action rejected; Passing time by 0.1  346
False
New action from the agent
Action

New action from the agent
Action rejected; Passing time by 0.1  465
False
New action from the agent
Action rejected; Passing time by 0.1  466
False
New action from the agent
Action rejected; Passing time by 0.1  467
False
New action from the agent
Action rejected; Passing time by 0.1  468
False
New action from the agent
Action rejected; Passing time by 0.1  469
False
New action from the agent
Action rejected; Passing time by 0.1  470
False
New action from the agent
Action rejected; Passing time by 0.1  471
False
New action from the agent
Action rejected; Passing time by 0.1  472
False
New action from the agent
Action rejected; Passing time by 0.1  473
False
New action from the agent
Action rejected; Passing time by 0.1  474
False
New action from the agent
Action rejected; Passing time by 0.1  475
False
New action from the agent
Action rejected; Passing time by 0.1  476
False
New action from the agent
Action rejected; Passing time by 0.1  477
False
New action from the agent
Action rejec

...

False
New action from the agent
Action rejected; Passing time by 0.1  14061
False
New action from the agent
Action rejected; Passing time by 0.1  14062
False
New action from the agent
Action rejected; Passing time by 0.1  14063
False
New action from the agent
Action rejected; Passing time by 0.1  14064
False
New action from the agent
Action rejected; Passing time by 0.1  14065
False
New action from the agent
Action rejected; Passing time by 0.1  14066
False
New action from the agent
Action rejected; Passing time by 0.1  14067
False
New action from the agent
Action rejected; Passing time by 0.1  14068
False
New action from the agent
Action rejected; Passing time by 0.1  14069
False
New action from the agent
Action rejected; Passing time by 0.1  14070
False
New action from the agent
Action rejected; Passing time by 0.1  14071
False
New action from the agent
Action rejected; Passing time by 0.1  14072
False
New action from the agent
Action rejected; Passing time by 0.1  14073
False
New ac

New action from the agent
Action rejected; Passing time by 0.1  14225
False
New action from the agent
Action rejected; Passing time by 0.1  14226
False
New action from the agent
Action rejected; Passing time by 0.1  14227
False
New action from the agent
Action rejected; Passing time by 0.1  14228
False
New action from the agent
Action rejected; Passing time by 0.1  14229
False
New action from the agent
Action rejected; Passing time by 0.1  14230
False
New action from the agent
Action rejected; Passing time by 0.1  14231
False
New action from the agent
Action rejected; Passing time by 0.1  14232
False
New action from the agent
Action rejected; Passing time by 0.1  14233
False
New action from the agent
Action rejected; Passing time by 0.1  14234
False
New action from the agent
Action rejected; Passing time by 0.1  14235
False
New action from the agent
Action rejected; Passing time by 0.1  14236
False
New action from the agent
Action rejected; Passing time by 0.1  14237
False
New action f

New action from the agent
Action rejected; Passing time by 0.1  14337
False
New action from the agent
Action rejected; Passing time by 0.1  14338
False
New action from the agent
Action rejected; Passing time by 0.1  14339
False
New action from the agent
Action rejected; Passing time by 0.1  14340
False
New action from the agent
Action rejected; Passing time by 0.1  14341
False
New action from the agent
Action rejected; Passing time by 0.1  14342
False
New action from the agent
Action rejected; Passing time by 0.1  14343
False
New action from the agent
Action rejected; Passing time by 0.1  14344
False
New action from the agent
Action rejected; Passing time by 0.1  14345
False
New action from the agent
Action rejected; Passing time by 0.1  14346
False
New action from the agent
Action rejected; Passing time by 0.1  14347
False
New action from the agent
Action rejected; Passing time by 0.1  14348
False
New action from the agent
Action rejected; Passing time by 0.1  14349
False
New action f

New action from the agent
Action rejected; Passing time by 0.1  14483
False
New action from the agent
Action rejected; Passing time by 0.1  14484
False
New action from the agent
Action rejected; Passing time by 0.1  14485
False
New action from the agent
Action rejected; Passing time by 0.1  14486
False
New action from the agent
Action rejected; Passing time by 0.1  14487
False
New action from the agent
Action rejected; Passing time by 0.1  14488
False
New action from the agent
Action rejected; Passing time by 0.1  14489
False
New action from the agent
Action rejected; Passing time by 0.1  14490
False
New action from the agent
Action rejected; Passing time by 0.1  14491
False
New action from the agent
Action rejected; Passing time by 0.1  14492
False
New action from the agent
Action rejected; Passing time by 0.1  14493
False
New action from the agent
Action rejected; Passing time by 0.1  14494
False
New action from the agent
Action rejected; Passing time by 0.1  14495
False
New action f

KeyboardInterrupt: 

In [ ]:
mean_reward, std_reward


### My Evaluation

Same code from testing environment section but I will just used the trained agent here. 

In [12]:
import gym
from gym import error, spaces, utils
from gym.utils import seeding
#random.seed(42)
envGym = CustomEnv()
obs = envGym.reset()
frames = [] # for animation

# Add another while loop above the current one for EPOCHS
while True: # This while is for one full cycle of products (20 nos, currently)

    # Choosing the action
    # Action from DQN agent
    action, _states = model.predict(obs)
    print("Action from DQN ", action)
    # Random action
    #action = envGym.action_space.sample()
    
    # Taking a step
    
    obs, reward, done, info = envGym.step(action) # the env here is gym
    # Note that in the above step function, i'm passing 1. 
    # It has no relevance to the action that will be taken. It is just to satisfy the OpenAI Gym requirements
    #print("Action chosen by the agent ", action)
    #print("Action taken by the environment ", )
    if done:
        print("Goal reached! ", "reward= ", reward)
        print("The env time is ", envGym.envSimpy.now)
        sum_Tardiness = 0 
        for i in range(20):
            #print(envGym.instances[i].tardiness)
            sum_Tardiness = sum_Tardiness + envGym.instances[i].tardiness
            print('Tardiness value of ', i, 'is ',envGym.instances[i].tardiness )
            
        print('Mean tardiness for this episode is ', sum_Tardiness)
        print('Total reward for this episode is ', envGym.cumulative_reward)
        break
    else:
        frames.append({
            'frame': envGym.render(mode='ansi'),
            'state': obs,
            'action': envGym.current_action,
            'reward': reward
            }
        )        

Action from DQN  1
New action from the agent
Start production of Product_0 at 0
Production time is 7
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
End production of Product_0 at 7
Action accepted
Start production of Product_1 at 7
Production time is 6
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
End production of Product_1 at 13
Action accepted
Start production of Product_2 at 13
Production time is 7
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
Action from DQN  0
New action from the agent
Action from 

Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  97
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  98
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  99
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  100
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  101
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  102
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  103
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  104
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  105
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  106
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  107
Action from DQN  1
New action from the agent
A

Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  207
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  208
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  209
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  210
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  211
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  212
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  213
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  214
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  215
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  216
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  217
Action from DQN  1
New action from the agen

Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  313
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  314
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  315
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  316
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  317
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  318
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  319
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  320
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  321
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  322
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  323
Action from DQN  1
New action from the agen

Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  410
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  411
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  412
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  413
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  414
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  415
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  416
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  417
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  418
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  419
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  420
Action from DQN  1
New action from the agen

...

Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14454
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14455
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14456
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14457
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14458
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14459
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14460
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14461
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14462
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14463
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14464
Action from DQN  1
Ne

Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14644
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14645
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14646
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14647
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14648
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14649
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14650
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14651
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14652
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14653
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14654
Action from DQN  1
Ne

Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14747
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14748
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14749
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14750
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14751
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14752
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14753
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14754
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14755
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14756
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14757
Action from DQN  1
Ne

Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14847
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14848
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14849
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14850
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14851
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14852
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14853
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14854
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14855
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14856
Action from DQN  1
New action from the agent
Action rejected; Passing time by 0.1  14857
Action from DQN  1
Ne

KeyboardInterrupt: 

### Other code

In [ ]:
# setting the machine_busy bit
        if envGym.machine.users != []:
            self.machine_busy = True
        else:
            self.machine_busy = False
        
        
        if self.machine_busy == True:
            self.reward = 0            
            # Run the simulation by 1 time unit
            self.next_time_stop += self.time_step
            self.envSimpy.run(until = self.next_time_stop)
            
            # Calculate states
            observation = self.getObservation() 
            done = self.doneFn()
            info = self.info
            self.cumulative_reward += self.reward
            print('\n')
            
        elif self.machine_busy == False:
            if self.current_action == 1: # if rejected don't enter the simulation
                # Rearrange the machine queue
                envGym.machine.queue = envGym.take_action()
                
                # Get the observation states
                observation = self.getObservation()
                done = self.doneFn()
                info = self.info
                
            else: # if accepted rearrange the queue and run simulation
                envGym.machine.queue = envGym.take_action()
                
                
                # Run the simulation by 1 time unit

### The entire environment code from Thursday, 10 December 2020 

In [ ]:
class CustomEnv(gym.Env):
    metadata = {'render.modes': ['human']}
    def __init__(self):
        super(CustomEnv, self).__init__()
        #random.seed(42)
        # Define action and observation space
        # They must be gym.spaces objects
        # Example when using discrete actions:

        # initially the observation space is zero. I will append as the products are initialized.
        #print("Observation space sample ",self.observation_space.sample())
        #self.observation_space = spaces.Box(low=0, high=255,shape=(2, 2), dtype=np.uint8)
##------------------------------------------------------------------------------------------------
##----------------------------------------SIMPY STUFF---------------------------------------------
##------------------------------------------------------------------------------------------------

        
#        self.action = env.process(self.production())
        self.NUM_PRODUCTS = 20
        self.next_time_stop = 0
        self.prod_and_requests = []
        self.reward = 0
        self.cumulative_reward = 0
        # Defining the observation and action spaces 
        # action space for choosing product 
        # self.action_space = spaces.Discrete(self.NUM_PRODUCTS)
        # action space for Yes/No action space 
        self.action_space = spaces.Discrete(2)
        self.observation_space = spaces.Box(0,1,shape = (self.NUM_PRODUCTS,),
                                            dtype = np.float32)
    
    def getObservation(self):
        # Calculate the states 
        states = []
        if self.machine.queue != None:
            for i in (self.machine.queue):
                states.append((self.relater(i)).number)
        #Checking the length of the states and filling the rest with zeros
        if len(states) < self.NUM_PRODUCTS:
            for i in range(self.NUM_PRODUCTS - len(states)):
                states.append(0)
        states = np.array(states).reshape(self.NUM_PRODUCTS,1)
        
        states = states.flatten()
        return states
    

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------OpenAI Gym functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    
    def step(self, action):
        
        print("-------------------------------------------------------------------------------")
        print("Action chosen by the RL agent ", action)
        
        # Define params
        self.current_action = action
        self.action_taken = False 
        self.info = {}
        print("Current user of the machine ", envGym.machine.users)
        print(envGym.machine.queue)
        
        

        self.next_time_stop += self.time_step
        self.envSimpy.run(until = self.next_time_stop)
        # Get the observation states
        observation = self.getObservation()
        done = self.doneFn()
        info = self.info
        
        return observation, self.reward, done, info
    
    # ----------------------------------------------------------------
    def reset(self):
        self.envSimpy = simpy.Environment()
        self.machine = simpy.Resource(self.envSimpy,capacity = 1)
        self.time_start = self.envSimpy.now
        self.next_time_stop = self.time_start + 2
        self.time_step = 1 
        self.time_step_terminal = self.time_start + 100
        self.current_action = 0
        self.instances = []
        
        for i in range(self.NUM_PRODUCTS):
            self.instances.append(self.product(self,self.envSimpy,'Product_%d' % i,i/100, self.machine))
        
        # i is divided by hundred because the number has to obey the observation_space criteria which is 1 to 1. 
        self.observation = self.getObservation()
        
        return np.array(self.observation)  # reward, done, info can't be included

    
    def render(self, mode='human'):
        myFrame = ""
        #myFrame = "_:_:_:_:_:_:_:_:01:19:18:_:01:02:03::|02|"
        
        for item in enumerate(self.machine.queue):
            product = self.relater(item[1])
            myFrame = str(int((product.number)*100)) +':'+ myFrame
        for i in range(self.NUM_PRODUCTS-len(self.machine.queue)):
            myFrame =  'x' +':' + myFrame
        if self.relater(self.machine.users[0]) == None:
            prod_in_machine = 0
            machine_text = prod_in_machine 
        else:
            prod_in_machine = self.relater(self.machine.users[0])
            machine_text = int(prod_in_machine.number*100)
        myFrame = myFrame +  "  |" + str(machine_text) + "|"
        return myFrame

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Miscellaneous functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    def doneFn(self):
        # So the condition is, 
        #(no items in queue1 + queue2 + ...) AND 
        #(no machine is running)
        
        if self.machine.queue != None:
            lenQueue = len(self.machine.queue)
        else:
            lenQueue = 0 
        lenMachinesUsed = self.machine.count
        if lenQueue == 0 and lenMachinesUsed == 0:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return True
        else:
            #print("length of queue ",lenQueue,"Machines used ", lenMachinesUsed)
            return False
        
    # A function to relate products and requests
    def relater(self,item):
        output_item = None
        # If the input is a request
        if type(item) == simpy.resources.resource.Request:
            for i, j in enumerate(self.prod_and_requests):
                if j[1] == item:
                    output_item = j[0]
                    return output_item
        else: #if the input is a product 
            for i, j in enumerate(self.prod_and_requests):
                if j[0] == item:
                    output_item = j[1]
                    return output_item    

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Action related functions--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------
    def choose_action(self):
        # sampling until we get a legal action
        self.action = envGym.action_space.sample()
        return self.action
    
    def take_action(self):
        # arrange the self.machine.queue based on the self.current_action
        self.action_taken = True 
        print("Taking the action....")
        print("Input machine queue ", self.machine.queue)
        if len(self.machine.queue) != 0:
            if self.current_action == 0: # if the answer is yes
                print("Action accepted")
                #print("The first item in the queue ", self.relater(self.machine.queue[0]).name, " is accepted ")
                print("Output machine queue ", self.machine.queue)
                return self.machine.queue # return the machine queue as is
            elif self.current_action == 1: # if the answer is no 
                # rearrange the machine queue 
                # Take the first element in the machine queue and put it in the last pos. 
                self.machine.queue.insert(len(self.machine.queue), self.machine.queue.pop(0))
                print("Action rejected")
                print("Output machine queue ", self.machine.queue)
                #print("The first item in the queue ", self.relater(self.machine.queue[0]).name, " is rejected ")
                return self.machine.queue
        else:
            return self.machine.queue

# --------------------------------------------------------------------------------------------------------------------------------
# -----------------------Product class definition--------------------------------------------------------------------
# --------------------------------------------------------------------------------------------------------------------------------

    class product(object):
        def __init__(self, envGym, envSimpy, name, number, machine):
            
            # Creating the required resources and environment
            self.envSimpy = envSimpy
            self.prod_type = random.randint(1,3) # the product type of the product.
            self.prod_state = 1 # the state of production. 1 implies raw material. 2 implies first operation done and so on. 
            self.production_time = random.randint(1,8)  
            self.name = name
            self.number = number
            self.machine = machine 
            self.production_end = random.randint(1,90)
            #self.action = self.envSimpy.process(self.production())
            #self.action_taken_event = envSimpy.event
            # Defining Events        
            #self.action_accepted_event = envSimpy.event()            
            # Defining processes
            #self.check_accepted_proc = envSimpy.process(self.check_accepted(envSimpy))


            
        def production(self):
            # the first step in production is requesting for a machine
            #print('entered production ' + self.name)
            with self.machine.request() as req:
                envGym.prod_and_requests.append([self,req])
                #print('waiting for the request to succeed ' + str(self.name))
                yield req
                print('Start production of ' + str(self.name) + ' at '+ str(self.envSimpy.now)  )
                print('Production time is ' + str(self.production_time))
                yield self.envSimpy.timeout(self.production_time)
                self.tardiness = self.production_end - self.envSimpy.now # +ve is good; -ve is bad 
                
                # End of production 
                print('End production of ' + str(self.name) + ' at ' + str(self.envSimpy.now))
                
                # Decide the reward 
                if self.tardiness > 0:
                    envGym.reward = 10 
                else: 
                    envGym.reward = 0
                    
                #yield self.action_accepted_event  # "passivate"
                
        
        def check_accepted(self, envSimpy): # sleep and production
            while True: # check in a continuous loop 
                if envGym.current_action == 0: # Is action accepted?
                    print("Action is accepted")
                    # Unsleeping the process 
                    self.action_accepted_event.succeed()
                    self.action_accepted_event = envSimpy.event()            
                else:
                    print("Action is rejected")
                    pass
        
        def passivate_production(self):
            while True:
                print("Passivating production at ", self.envSimpy.now)
                yield self.reactivate_production
                print("Production reactivate at ", self.envSimpy.now)
            #print('Remaining products to produce ')
            #print((self.machine.queue)) 